In [1]:
%matplotlib inline
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.autograd as autograd
import dataset as dataset
import datapreparation as datp
import numpy as np
import matplotlib.pyplot as plt
import random
import math
import os
import copy
import importlib
import GRU as gru

In [6]:
## reload imports
importlib.reload(datp)
importlib.reload(gru)
data = dataset.pianoroll_dataset_batch("C:\DeepLearning\Master\\neural-composer-assignement\datasets\\training\piano_roll_fs5")
print(torch.cuda.is_available())

True


In [7]:
## Initialize Generalist
## Generalist(input_size, hidden_size, num_tags)
model_generalist = gru.Generalist(128, 256, int(data.num_tags()))
model_generalist.optimizer = torch.optim.Adam(model_generalist.parameters())
model_generalist.loss_log = []

In [107]:
## Initialize Specialist
## Specialist(input_size, hidden_size, num_tags)
model_specialist = gru.Specialist(128, 256, int(data.num_tags()))
#model_specialist.cuda()
#model_specialist.optimizer = torch.optim.Adam(model_specialist.parameters())
model_specialist.loss_log = []

In [ ]:
## Train the generalist
num_epochs = 1000
## Returns state for transferred training
state = gru.train_sequence(model_generalist, num_epochs, data, model_generalist.optimizer, model_generalist.loss_log)

In [ ]:
## Train the specialist
num_epochs = 100
## Returns state for transferred training
state = gru.train_sequence(model_specialist, num_epochs, data, model_specialist.optimizer, model_specialist.loss_log)


In [8]:
## Save the Generalist state
dir_path = os.path.dirname(os.path.realpath(gru.__file__))
torch.save(state, dir_path+'\\Generalist.pt')

## Current best state 1000 epochs, 256 hidden_size.

In [76]:
## Save the Specialist state
dir_path = os.path.dirname(os.path.realpath(gru.__file__))
torch.save(state, dir_path+'\\Specialist.pt')

## Current best state 1000 epochs, 256 hidden_size.

In [10]:
## Print Generalist state
print('Total number of epochs run: ', len(model_generalist.loss_log))
print('Epoch number of lowest loss: ', model_generalist.loss_log.index(min(model_generalist.loss_log)))
print('Loss for best epoch', min(model_generalist.loss_log))

Total number of epochs run:  1000
Epoch number of lowest loss:  989
Loss for best epoch 1.0233720755204558


In [78]:
## Print Specialist state
print('Total number of epochs run: ', len(model_specialist.loss_log))
print('Epoch number of lowest loss: ', model_specialist.loss_log.index(min(model_specialist.loss_log)))
print('Loss for best epoch', min(model_specialist.loss_log))

Total number of epochs run:  1500
Epoch number of lowest loss:  1469
Loss for best epoch 0.8508922294713557


In [8]:
## Load saved weights into Generalist model
#gru.load(model_generalist, model_generalist.optimizer, filename='Generalist.pt')
model_generalist.optimizer = gru.load(model_generalist, filename='Generalist.pt')
## Additional weight setting with dropout used. Different result, but needs to train longer.
#gru.load(model_generalist, model_generalist.optimizer, filename='GeneralistDropout.pt')
#model_generalist.optimizer = gru.load(model_generalist, filename='GeneralistDropout.pt')

In [12]:
## Generate Generalist music
embed, matrix = gru.gen_music_seconds_smooth(model_generalist, data[0][0] ,composer=0,fs=5,gen_seconds=16,init_seconds=2, device='cpu')
embed



#matrix *= 100
#datp.piano_roll_to_mid_file(matrix,"output.mid",1,74) # 16 Organ

# Export pianoroll as CSV

In [14]:
import numpy
roll = matrix.astype(int)
numpy.savetxt("test.csv", roll, fmt='%i', delimiter=";")

# Convert csv to midi

In [14]:
roll *= 100
datp.piano_roll_to_mid_file(roll,"test2.mid",5,1)

'C:\\DeepLearning\\Master\\neural-composer-assignement\\helpers\\test2.mid'

In [108]:
## Load saved weights into Specialist model
model_specialist.optimizer = gru.load(model_specialist, filename='Specialist.pt', device='cuda')
#model_specialist.optimizer = gru.load(model_specialist, filename='Specialist-256-not-shit.pt', device='cuda')

In [80]:
## Generate Specialist music
embed, matrix = gru.gen_music_seconds_smooth(model_specialist, data[0][0] ,composer=0,fs=5,gen_seconds=40,init_seconds=5, device='cpu')


NameError: name 'model_specialist' is not defined

In [7]:
#datp.piano_roll_to_mid_file("C:\DeepLearning\Master\IP\fourpart\test.csv","test",1,11)
data2 = dataset.pianoroll_dataset_batch("C:\DeepLearning\Master\\IP\\fourpart\\output")
print(data2[0][0].shape[2])
#data2.view_pianoroll(0)
datp.visualize_piano_roll(data2.data[0],fs=1)
play, matrix = datp.embed_play_v1(data2.data[0],fs=1)
play

#matrix *= 100
#datp.piano_roll_to_mid_file(matrix,"output.mid",1,74) # 16 Organ

128


In [11]:
for i in range(1, 11):
    data2 = dataset.pianoroll_dataset_batch("C:\DeepLearning\Master\\IP\\fourpart\\output")
    print(data2[i][0].shape[2])
    play, matrix = datp.embed_play_v1(data2.data[i],fs=1)
    
    
    matrix *= 100
    datp.piano_roll_to_mid_file(matrix,"test"+str(i)+".mid",1,74)

128
128
128
128
128
128
128
128
128
128
